# Using INTF geometry for NBE1 in Rison et al. 2016

## Initialization

In [1]:
using Pkg
Pkg.activate(".")
Pkg.instantiate()

using StaticArrays
using LinearAlgebra
using DelimitedFiles

# This is a package to compute the fields created by TLs.
# It works by decomposing a TL into a large number of small dipoles
# that radiate with different phases and amplitudes.
using DipoleRadiators

#initplot(:jupyter)
using Plots
theme(:vibrant)
plotly(frame=:box, linewidth=2.0)

"""
Set up a MTLE the transmission line as a union of dipoles.

The orientation of the TL is defined by `ϕ` and `θ` 
(both zero for a vertical TL).  `H2` is the peak altitude of the TL
(the current injection point), `Z0` is the TL extension, `Ipk` is
the peak current amplitude, `τ1` and `τ2` are the characteristic times
of the current waveform, `v` and `v1` are the downward and upward 
velocities, `λ` and `λ1` are the downward and upward attenuation 
lengths, `γ` is an additional attenuation (γ=1 matches the 
down and up currents) and Δτ is an additional phase difference
between the two pulses.  The upward pulse (reflection) is considered
only if `bounce` is `true`.
"""
function channel(;ϕ=0.0, θ=0.0, H2=6e3, Z0=455, λ=900.0, Ipk=51.5e3,
                 τ1=1e-6, τ2=5e-6, v=3.5e7,
                 v1=v, λ1=λ,
                 γ=1.0, Δτ=0.0,
                 bounce=false)
    H1 = H2 - Z0
    
    # Unit vector in the channel direction
    sinϕ, cosϕ = sincos(ϕ)
    sinθ, cosθ = sincos(θ)
    
    u = @SVector [cosϕ * sinθ, sinϕ * sinθ, cosθ]

    # Init and end point of the TL.  I think this is the convention used in
    # the draft.
    r2 = @SVector [0, 0, u[3] * H1]
    r1 = @SVector [u[1] * Z0, u[2] * Z0, u[3] * H2]
    
    # Current pulse
    α, β = 1 / τ1, 1 / τ2

    # Note that here the positive sign of I is from r0 to r1 so since the altitude
    # of r0 is higher than that of r1 and the pulse propagates down we need a
    # positive current.
    I0 = Ipk * (1 + α / β) * (α / β)^(-α / (α + β))

    pulse = CurrentPulse(t -> I0 * (exp(α * t) / (1 + exp((α + β) * t))),
                         -max(τ1, τ2) * 5,
                         max(τ1, τ2) * 20,
                         min(τ1, τ2) / 10)
    
    # This sets an MTLE from r1 to r2 with 1000 dipoles.  mirror means whether
    # to include the ground reflection at z=0.
    tl0 = mtle(pulse, r1, r2, v, λ, 1000, mirror=true)
    bounce || return tl0

    # If bounce is true we set a second transmission line joined to the first
    # where the pulse goes upwards now.
    r3 = r1
    
    tl1 = mtle(pulse, r2, r3, v1, λ1, 1000,
               mirror=true,

               # The minus sign is needed because the convention is that
               # positive current goes from r2 to r3 but we want the current
               # to be in the same direction as in the first ML.
               # exp(-Z0 / λ) is the attenuation in the first ML
               # γ is an optional additional attenuation
               w0=-γ * exp(-Z0 / λ),

               # Z0 / v is the phase introduced by the first ML
               # Δτ is an optional additional phase.
               t0=Z0 / v + Δτ)

    tl = (tl0, tl1)
    
    tl
end

 Activating environment at `~/projects/dongshuai/dipoles/RisonNBE/Project.toml`
  Installed Widgets ──────── v0.6.3
  Installed Mux ──────────── v0.7.6
  Installed StaticArrays ─── v1.2.2
  Installed ChainRulesCore ─ v0.10.2
  Installed TOML ─────────── v1.0.3
  Installed Plots ────────── v1.16.2
  Installed Distributions ── v0.24.18
  Installed OffsetArrays ─── v1.9.2
  Installed NetworkOptions ─ v1.2.0
  Installed JSExpr ───────── v0.5.3
  Installed OptimBase ────── v2.0.2
  Installed LazyArtifacts ── v1.3.0
  Installed Plotly ───────── v0.4.0
┌ Info: Precompiling StaticArrays [90137ffa-7385-5640-81b9-e52037218182]
└ @ Base loading.jl:1278
┌ Info: Precompiling DipoleRadiators [15980006-e03e-44c8-ba4d-57a4922ddbba]
└ @ Base loading.jl:1278
┌ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]
└ @ Base loading.jl:1278
┌ Info: For saving to png with the Plotly backend PlotlyBase has to be installed.
└ @ Plots /Users/luque/.julia/packages/Plots/QaOSg/src/backends.jl:372


channel

## NBE1

In [2]:
# Load observational data
tdata, ydata = eachcol(readdlm("data/NBE1.dat"));

# The code expects time in s
tdata .*= 1e-6
plot(tdata / 1e-6, ydata, label="NBE1", color=:black, xlabel="time (us)", ylabel="Electric field (V/m)")

<!DOCTYPE html>
 
 
 Plots.jl

### No reflection

Here the results look identical to those in `NBE1_no_reflection.ps`.

In [3]:
tdata, ydata = eachcol(readdlm("data/NBE1.dat"));
tdata .*= 1e-6

t = range(2e-5, stop=7e-5, length=1000);
robs = @SVector [5.5e3, 0, 0];

@time tl = channel(Ipk=51.5e3, λ=900, τ1=1e-6, τ2=5e-6)
@time ef = fields(tl, robs, t);

plot(tdata * 1e6, ydata, label="NBE1", color=:black, xlabel="time (us)", ylabel="Electric field (V/m)");
plot!(t * 1e6 .- 20, total(ef, 3), label="total", lw=2.0);
plot!(t * 1e6 .- 20, static(ef, 3), label="static");
plot!(t * 1e6 .- 20, induction(ef, 3), label="induction");
plot!(t * 1e6 .- 20, radiation(ef, 3), label="radiation")

  0.154405 seconds (551.60 k allocations: 28.988 MiB)
  1.048778 seconds (2.60 M allocations: 131.306 MiB, 3.56% gc time)


<!DOCTYPE html>
 
 
 Plots.jl

### Parameters from Fig. 3c in the paper

In [5]:
tdata, ydata = eachcol(readdlm("data/NBE1.dat"));
tdata .*= 1e-6

t = range(2e-5, stop=7e-5, length=1000);
robs = @SVector [5.5e3, 0, 0];

# Extension of the TL
Z0 = 455.

# Upward/Downward times.  These are obtained from the INTF sources.
td, tu = 8e-6, 6e-6

# Upward/Downward velocities
v, v1 = Z0 / td, Z0 / tu


@time tl = channel(    
    # Length of the TL (given above)
    Z0=Z0,
    
    # Peak current
    Ipk=31.4e3, 
    
    # Downward attenuation length
    λ=273.7, 
    
    # Upward attenuation length
    λ1=57.8,
    
    # Upward/downward velocities (given above)
    v=v, 
    v1=v1,
    
    # τ1/τ2 in the current waveform
    τ1=0.8e-6, 
    τ2=14.2e-6,
    
    bounce=true)
@time ef = fields(tl, robs, t);

plot(tdata * 1e6, ydata, label="NBE1", color=:black, xlabel="time (us)", ylabel="Electric field (V/m)");
plot!(t * 1e6 .- 20, total(ef, 3), label="total", lw=2.0);
plot!(t * 1e6 .- 20, static(ef, 3), label="static");
plot!(t * 1e6 .- 20, induction(ef, 3), label="induction");
plot!(t * 1e6 .- 20, radiation(ef, 3), label="radiation")

LoadError: UndefVarError: H2 not defined

In [51]:
tdata, ydata = eachcol(readdlm("data/NBE1.dat"));
tdata .*= 1e-6

dis = 5.5e3
H2 = dis * tan(deg2rad(50.8))
H1 = dis * tan(deg2rad(47.3))
Z0 = H2 - H1

t = range(2e-5, stop=7e-5, length=1000);
robs = @SVector [dis, 0, 0];
delay = 2e-6

# Upward/Downward times.  These are obtained from the INTF sources.
td, tu = 10.3e-6 + delay, 16.7e-6 - delay

# Upward/Downward velocities
v, v1 = Z0 / td, Z0 / tu


@time tl = channel(
    # Uppermost altitude
    H2=H2,

    # Length of the TL (given above)
    Z0=Z0,
    
    # Peak current
    Ipk=31.4e3, 
    
    # Downward attenuation length
    λ=273.7, 
    
    # Upward attenuation length
    λ1=57.8,
    
    # Upward/downward velocities (given above)
    v=v, 
    v1=v1,
    
    # τ1/τ2 in the current waveform
    τ1=0.7e-6, 
    τ2=20e-6,
    
    bounce=true)
@time ef = fields(tl, robs, t);

plot(tdata * 1e6, ydata, label="NBE1", color=:black, xlabel="time (us)", ylabel="Electric field (V/m)");
plot!(t * 1e6 .- 22, total(ef, 3), label="total", lw=2.0);
plot!(t * 1e6 .- 22, static(ef, 3), label="static");
plot!(t * 1e6 .- 22, induction(ef, 3), label="induction");
plot!(t * 1e6 .- 22, radiation(ef, 3), label="radiation")

  0.000813 seconds (34 allocations: 1.508 MiB)
  0.080080 seconds (211 allocations: 403.969 KiB)


<!DOCTYPE html>
 
 
 Plots.jl

In [57]:
using LsqFit

tdata, ydata = eachcol(readdlm("data/NBE1.dat"));
tdata .*= 1e-6

dis = 5.5e3
H2 = dis * tan(deg2rad(50.8))
H1 = dis * tan(deg2rad(47.3))
Z0 = H2 - H1

t = range(2e-5, stop=7e-5, length=1000);
robs = @SVector [dis, 0, 0];
delay = 2e-6

# Upward/Downward times.  These are obtained from the INTF sources.
td, tu = 10.3e-6 + delay, 16.7e-6 - delay

# Upward/Downward velocities
v, v1 = Z0 / td, Z0 / tu



# Multiplicative factors to handle parameters of order unity
m = [1e-6, 1e3, 100, 100, 1e-7, 1e-7]

γ = 1
function model(t, p)
    shift, Ipk, λ, λ1, τ1, τ2 = p .* m
    tl = channel(H2=H2, Z0=Z0, Ipk=Ipk, τ1=τ1, τ2=τ2, v=v, v1=v1, 
        λ=λ, λ1=λ1, γ=γ, bounce=true);
    ef = fields(tl, robs, t .+ shift);
    return total(ef, 3)
end

p0 = [22e-6, 31.4e3, 800.0, 800.0, 0.4e-6, 20e-6] 
@time fit = curve_fit(model, tdata[1:10:end], ydata[1:10:end], p0 ./ m)

# Print the fitted parameters
for (sym, val) in zip([:shift, :Ipk, :λ, :λ1, :τ1, :τ2], coef(fit) .* m) 
    println(sym => val)
end;

# Now plot them
shift, Ipk, λ, λ1, τ1, τ2 = coef(fit) .* m
tl = channel(H2=H2, Z0=Z0, Ipk=Ipk, τ1=τ1, τ2=τ2, v=v, v1=v1, 
            λ=λ, λ1=λ1, γ=γ, bounce=true);

@time ef = fields(tl, robs, t);
t1 = t .- shift
plot(tdata * 1e6, ydata, label="NBE1", color=:black, xlabel="time (us)", ylabel="Electric field (V/m)");
plot!(t1 * 1e6, total(ef, 3), label="total", lw=2.0);
plot!(t1 * 1e6, static(ef, 3), label="static");
plot!(t1 * 1e6, induction(ef, 3), label="induction");
plot!(t1 * 1e6, radiation(ef, 3), label="radiation")

 23.115463 seconds (281.24 k allocations: 768.622 MiB, 0.32% gc time)
:shift => 2.1685901656755017e-5
:Ipk => 28473.033587751408
:λ => 395.9690910569822
:λ1 => 857.2713522213687
:τ1 => 7.740549505927158e-7
:τ2 => 7.246588276594559e-6
  0.072888 seconds (214 allocations: 405.266 KiB)


<!DOCTYPE html>
 
 
 Plots.jl